In [1]:
import pandas as pd
import gzip
import json

In [1]:
def parse(path):
    with gzip.open(path, 'rb') as g:
        for l in g:
            yield json.loads(l)

def getDF(path):
    i = 0
    df = {}
    for d in parse(path):
        df[i] = d
        i += 1
    return pd.DataFrame.from_dict(df, orient='index')

ratings = getDF('XXXXXXXX/reviews_Beauty_5.json.gz')

ratings.rename(columns={'reviewerID': 'user_id', 
                        'asin': 'item_id', 
                        'reviewerName': 'user_name', 
                        'reviewText': 'review_text',
                        'summary': 'review_summary',
                        'overall': 'score'},
               inplace=True)

ratings['user_emb_id'] = ratings.user_id.astype('category').cat.codes.values + 1
ratings['item_emb_id'] = ratings.item_id.astype('category').cat.codes.values + 1

NameError: name 'gzip' is not defined

In [15]:
ratings.sample(5)

user_id     item_id  user_name helpful  \
13409    AC8C9PT59CDW1  B0009OAI8G     M.A.R.  [1, 1]   
92567   A2001U1WVA2ZZF  B003OGT4KE    Ruta 70  [0, 0]   
142399   ASSGY9U4DMNS0  B0071Q5PL0  camgirl25  [1, 4]   
110281  A2JLYOGJHC5X3T  B004KRVE22    A. King  [0, 0]   
110547   AVUTED3DZLJX6  B004L96O4W    cesca86  [0, 0]   

                                              review_text  score  \
13409   This is my 2nd order of this powder as I am ho...    5.0   
92567   This is a wonderful color, especially when pla...    5.0   
142399  I don't really know how i feel about this prod...    2.0   
110281  Salon effects are one of my beauty must haves....    1.0   
110547  When I switched to using more natural products...    4.0   

             review_summary  unixReviewTime   reviewTime  user_emb_id  \
13409           Great scent      1330732800   03 3, 2012        18540   
92567   Just as it looks!!!      1362873600  03 10, 2013         5845   
142399                 soso      1363737600  03 20, 2013        21224   
110281              No good      1374710400  07 25, 2013         9102   
110547     Scent is amazing      1400198400  05 16, 2014        21709   

        item_emb_id  
13409           807  
92567          6242  
142399         9240  
110281         7370  
110547         7402

In [16]:
len(ratings['user_emb_id']), len(ratings['user_emb_id'].unique()), len(ratings['item_emb_id']), len(ratings['item_emb_id'].unique())

(198502, 22363, 198502, 12101)

In [17]:
len(ratings)

198502

In [21]:
ratings_sorted = ratings.sort_values(by=['user_emb_id', 'unixReviewTime'])
user_item_mapping = ratings_sorted.groupby('user_emb_id')['item_emb_id'].agg(list).reset_index()

user_item_mapping = user_item_mapping[user_item_mapping['item_emb_id'].apply(len) > 1]
item_counts = ratings_sorted['item_emb_id'].value_counts()
items_to_keep = item_counts[item_counts >= 5].index
user_item_mapping['item_emb_id'] = user_item_mapping['item_emb_id'].apply(lambda x: [item for item in x if item in items_to_keep])
user_item_mapping = user_item_mapping[user_item_mapping['item_emb_id'].apply(len) > 0]

user_item_mapping.rename(columns={'item_emb_id': 'clicked_items'}, inplace=True)
average_click_sequence_length = user_item_mapping['clicked_items'].apply(len).mean()

In [22]:
user_item_mapping

user_emb_id                                      clicked_items
0                1           [9450, 9840, 10077, 11156, 11753, 11864]
1                2                [3310, 4573, 9080, 4137, 10956, 59]
2                3  [4209, 4387, 6363, 454, 5666, 8650, 8877, 9405...
3                4  [8969, 10131, 8824, 8651, 10148, 3496, 9767, 1...
4                5       [8936, 5098, 8072, 8347, 10163, 8824, 10228]
...            ...                                                ...
22358        22359                        [6398, 2823, 353, 42, 8289]
22359        22360                  [10368, 3849, 40, 444, 9673, 664]
22360        22361  [4142, 4860, 5049, 5564, 5906, 7206, 10368, 10...
22361        22362                   [2895, 10101, 11039, 6630, 6701]
22362        22363                [9215, 447, 2083, 7057, 8524, 8646]

[22363 rows x 2 columns]

In [23]:
average_click_sequence_length

8.876358270357287

In [24]:
# train_set and test_set
from sklearn.model_selection import train_test_split
train_data, test_data = train_test_split(user_item_mapping, test_size=0.1, random_state=42)

# Optionally, you can reset the index for both train and test datasets
train_data.reset_index(drop=True, inplace=True)
test_data.reset_index(drop=True, inplace=True)
len(train_data)

20126

In [25]:
all_train_seq = []
for session in train_data['clicked_items']:
    all_train_seq.append(session[:-1])

all_test_seq = []
for session in test_data['clicked_items']:
    all_test_seq.append(session[:-1])

In [28]:
# with open("process_MSGIFSR/beauty_1/train.txt", "w") as f:
#     for row in all_train_seq:
#         line = ", ".join(map(str, row))
#         f.write(line + "\n")
# with open("process_MSGIFSR/beauty_1/test.txt", "w") as f:
#     for row in all_test_seq:
#         line = ", ".join(map(str, row))
#         f.write(line + "\n")

In [187]:
def sequence_split(item_sequence):
    sequences = []
    for i in range(1, len(item_sequence)):
        input_sequence = item_sequence[:i] 
        target_item = item_sequence[i]
        sequences.append((input_sequence, target_item))
    return sequences

In [188]:
# segment train_set
train_data['sequence_splits'] = train_data['clicked_items'].apply(sequence_split)
train_flattened_sequences = []
for seq in train_data['sequence_splits']:
    train_flattened_sequences.extend(seq)
split_df = pd.DataFrame(train_flattened_sequences, columns=['input_sequence', 'target_item'])

train_sequences = [[],[]]
for _, row in split_df.iterrows():
    train_sequences[0].append(row['input_sequence'])
    train_sequences[1].append(row['target_item'])
len(train_sequences[0])

158717

In [189]:
# segment test_set
test_data['sequence_splits'] = test_data['clicked_items'].apply(sequence_split)
test_flattened_sequences = []
for seq in test_data['sequence_splits']:
    test_flattened_sequences.extend(seq)
split_df = pd.DataFrame(test_flattened_sequences, columns=['input_sequence', 'target_item'])

test_sequences = [[],[]]
for _, row in split_df.iterrows():
    test_sequences[0].append(row['input_sequence'])
    test_sequences[1].append(row['target_item'])
len(test_sequences[0])

17422

In [192]:
import pickle
from collections import defaultdict, Counter
with open('train_beauty.txt', 'wb') as f:
    pickle.dump(train_sequences, f)
with open('test_beauty.txt', 'wb') as f:
    pickle.dump(test_sequences, f)
with open('all_beauty.txt', 'wb') as f:
    pickle.dump(all_train_seq, f)

In [109]:
def parse2(path):
  g = gzip.open(path, 'r')
  for l in g:
    yield json.dumps(eval(l))

f = open("output.strict", 'w')
for l in parse2("XXXXXXXXX/meta_Beauty.json.gz"):
  f.write(l + '\n')
meta_data = load_data('output.strict')

In [110]:
def extract_asin_reviewer(data):
    meta_data = defaultdict(list)
    for entry in data:
        # entry = json.dumps(entry, ensure_ascii=False, indent=4)
        # entry = json.loads(entry)
        asin = entry.get('asin')
        title = entry.get('title', None)

        meta_data[asin].append({'title': title})
    return meta_data

In [199]:
from collections import defaultdict, Counter
extract_meta_data = extract_asin_reviewer(meta_data)
extract_meta_data

defaultdict(list,
            {'0205616461': [{'title': 'Bio-Active Anti-Aging Serum (Firming Ultra-Hydrating Serum)'}],
             '0558925278': [{'title': 'Eco Friendly Ecotools Quality Natural Bamboo Cosmetic Mineral Brush Set Kit of 4 Soft Brushes and 1 Pouch Baby Kabuki Eye Shading Brush Mineral Powder Brush Concealer Brush(travle Size)'}],
             '0733001998': [{'title': 'Mastiha Body Lotion'}],
             '0737104473': [{'title': 'Hello Kitty Lustre Lipstick (See sellers comments for colors)'}],
             '0762451459': [{'title': 'Stephanie Johnson Mermaid Round Snap Mirror'}],
             '1304139212': [{'title': 'Set of 2 MAC Lip Care - Lip Pencil - Auburn'}],
             '130414674X': [{'title': 'Set of 2 Benefit She Laq Makeup Sealer'}],
             '130414089X': [{'title': 'New Benefit Waterproof Automatic Eyeliner Pen - Black - BAD Gal Liner'}],
             '1304196062': [{'title': 'Max Factor Lasting Performance Foundation -Pastelle 102 35ml'}],
         

In [200]:
item_dict = dict(zip(ratings['item_emb_id'], ratings['item_id']))
item_dict

{1: '7806397051',
 2: '9759091062',
 3: '9788072216',
 4: '9790790961',
 5: '9790794231',
 6: 'B00004TMFE',
 7: 'B00004TUBL',
 8: 'B00004TUBV',
 9: 'B00004U9UY',
 10: 'B00004U9V2',
 11: 'B000050B6U',
 12: 'B000052WY7',
 13: 'B000052WYD',
 14: 'B000052WYL',
 15: 'B000052WYN',
 16: 'B000052X9G',
 17: 'B000052XIA',
 18: 'B000052XW5',
 19: 'B000052XYQ',
 20: 'B000052XZP',
 21: 'B000052XZX',
 22: 'B000052Y25',
 23: 'B000052Y33',
 24: 'B000052Y5F',
 25: 'B000052Y6Z',
 26: 'B000052YJC',
 27: 'B000052YJD',
 28: 'B000052YJH',
 29: 'B000052YJM',
 30: 'B000052YJX',
 31: 'B000052YKI',
 32: 'B000052YKM',
 33: 'B000052YKS',
 34: 'B000052YKY',
 35: 'B000052YL1',
 36: 'B000052YLX',
 37: 'B000052YM0',
 38: 'B000052YM3',
 39: 'B000052YM4',
 40: 'B000052YM7',
 41: 'B000052YM8',
 42: 'B000052YMG',
 43: 'B000052YMQ',
 44: 'B000052YMR',
 45: 'B000052YMS',
 46: 'B000052YMT',
 47: 'B000052YMV',
 48: 'B000052YMX',
 49: 'B000052YN5',
 50: 'B000052YN7',
 51: 'B000052YOL',
 52: 'B000052YOR',
 53: 'B000052YOX',
 5

In [195]:
len(item_dict)

12101

In [196]:
all_items = set()

In [201]:
train_prompts = []
for items in train_sequences[0]:
    item_prompts = []
    for idx,item in enumerate(items, start=1):
        if item_dict[item] in extract_meta_data:
            title = extract_meta_data[item_dict[item]][0]['title']
            all_items.add(title)
            item_prompts.append(f"{idx}.{title}_{item} \n ")
    prompt_text = "The order in which users click on items is as follows: " + "".join(item_prompts) 
    train_prompts.append({"prompt": prompt_text})
train_prompts

[{'prompt': 'The order in which users click on items is as follows: 1.Olay Regenerist 14-Day Skin Intervention_2802 \n '},
 {'prompt': 'The order in which users click on items is as follows: 1.Olay Regenerist 14-Day Skin Intervention_2802 \n 2.Max Factor Panstik Foundation - 13 Nouveau Beige_3961 \n '},
 {'prompt': 'The order in which users click on items is as follows: 1.Olay Regenerist 14-Day Skin Intervention_2802 \n 2.Max Factor Panstik Foundation - 13 Nouveau Beige_3961 \n 3.Olay Professional Pro-X Deep Wrinkle Treatment Anti Aging 1.0 Fl Oz_4048 \n '},
 {'prompt': 'The order in which users click on items is as follows: 1.Olay Regenerist 14-Day Skin Intervention_2802 \n 2.Max Factor Panstik Foundation - 13 Nouveau Beige_3961 \n 3.Olay Professional Pro-X Deep Wrinkle Treatment Anti Aging 1.0 Fl Oz_4048 \n 4.OPI Nail Envy Matte, 0.5-Fluid Ounce_3394 \n '},
 {'prompt': 'The order in which users click on items is as follows: 1.Olay Regenerist 14-Day Skin Intervention_2802 \n 2.Max Fac

In [202]:
test_prompts = []
for items in test_sequences[0]:
    item_prompts = []
    for idx,item in enumerate(items, start=1):
        if item_dict[item] in extract_meta_data:
            title = extract_meta_data[item_dict[item]][0]['title']
            all_items.add(title)
            item_prompts.append(f"{idx}.{title}_{item} \n ")
    prompt_text = "The order in which users click on items is as follows: " + "".join(item_prompts)
    test_prompts.append({"prompt": prompt_text})
test_prompts

[{'prompt': 'The order in which users click on items is as follows: 1.Zia Bamboo Exfoliant, 1.6 Ounce Bottles (Pack of 12)_2664 \n '},
 {'prompt': 'The order in which users click on items is as follows: 1.Zia Bamboo Exfoliant, 1.6 Ounce Bottles (Pack of 12)_2664 \n 2.Remington S1051 Salon Quality, Professional Ceramic Hair Straightener_4151 \n '},
 {'prompt': 'The order in which users click on items is as follows: 1.Zia Bamboo Exfoliant, 1.6 Ounce Bottles (Pack of 12)_2664 \n 2.Remington S1051 Salon Quality, Professional Ceramic Hair Straightener_4151 \n 3.Sunburnt Therapeutic After Sun Relief, 6-Ounce Tube_3889 \n '},
 {'prompt': 'The order in which users click on items is as follows: 1.Zia Bamboo Exfoliant, 1.6 Ounce Bottles (Pack of 12)_2664 \n 2.Remington S1051 Salon Quality, Professional Ceramic Hair Straightener_4151 \n 3.Sunburnt Therapeutic After Sun Relief, 6-Ounce Tube_3889 \n 4.Vaseline Men Body and Face Lotion , 20.3 Ounce Bottle (Pack of 3)_3714 \n '},
 {'prompt': 'The ord

In [84]:
with open('XXXXXXXXXXXX/train_prompt_mul.json', 'w', encoding='utf-8') as f:
        json.dump(train_prompts, f, ensure_ascii=False, indent=4)
with open('XXXXXXXXXXXX/test_prompt_mul.json', 'w', encoding='utf-8') as f:
        json.dump(test_prompts, f, ensure_ascii=False, indent=4)

In [85]:
import pickle
with open('XXXXXXXXXXXX/all_items.txt', 'wb') as f:
    pickle.dump(all_items, f)

In [97]:
import torch
train_candidate_items = pickle.load(open('XXXXXXXXXXXX/train_candidate_items.txt', 'rb'))

In [126]:
train_candidate_text = []
for candidate_items in train_candidate_items:
    candidate_item = []
    for item in candidate_items:
        if item_dict[item + 1] in extract_meta_data:
            title = extract_meta_data[item_dict[item + 1]][0]['title']
            candidate_item.append(title)
    train_candidate_text.append(candidate_item)
len(train_candidate_text)

158717

In [130]:
len(train_sequences[0])

158717

In [213]:
train_prompts_with_candidate = []
train_candidates = []
for items in train_candidate_text:
    candidate_prompts = []
    for idx,item in enumerate(items, start=1):
        candidate_prompts.append(f"{idx}.{item} \n ")
    train_candidates.append(candidate_prompts)
index = 0
train_text_items = []
for items in train_sequences[0]:
    item_prompts = []
    train_text_item = []
    for idx,item in enumerate(items, start=1):
        if item_dict[item] in extract_meta_data:
            title = extract_meta_data[item_dict[item]][0]['title']
            train_text_item.append(title)
            all_items.add(title)
            item_prompts.append(f"{idx}.{title}_{item} \n ")
    train_text_items.append(train_text_item)
    prompt_text = "".join(item_prompts)
    candidate_text = "".join(train_candidates[index])
    train_prompts_with_candidate.append({"Current session interactions": prompt_text, "Candidate item set": candidate_text})
    index += 1
train_text_items

[['Olay Regenerist 14-Day Skin Intervention'],
 ['Olay Regenerist 14-Day Skin Intervention',
  'Max Factor Panstik Foundation - 13 Nouveau Beige'],
 ['Olay Regenerist 14-Day Skin Intervention',
  'Max Factor Panstik Foundation - 13 Nouveau Beige',
  'Olay Professional Pro-X Deep Wrinkle Treatment Anti Aging 1.0 Fl Oz'],
 ['Olay Regenerist 14-Day Skin Intervention',
  'Max Factor Panstik Foundation - 13 Nouveau Beige',
  'Olay Professional Pro-X Deep Wrinkle Treatment Anti Aging 1.0 Fl Oz',
  'OPI Nail Envy Matte, 0.5-Fluid Ounce'],
 ['Olay Regenerist 14-Day Skin Intervention',
  'Max Factor Panstik Foundation - 13 Nouveau Beige',
  'Olay Professional Pro-X Deep Wrinkle Treatment Anti Aging 1.0 Fl Oz',
  'OPI Nail Envy Matte, 0.5-Fluid Ounce',
  'Olay Skin Tightening Serum 1 Fl Oz'],
 ['Olay Regenerist 14-Day Skin Intervention',
  'Max Factor Panstik Foundation - 13 Nouveau Beige',
  'Olay Professional Pro-X Deep Wrinkle Treatment Anti Aging 1.0 Fl Oz',
  'OPI Nail Envy Matte, 0.5-Fluid

In [204]:
test_candidate_items = pickle.load(open('XXXXXXXXXXX/test_candidate_items.txt', 'rb'))
test_candidate_items

[[2663,
  2419,
  3248,
  3181,
  1449,
  2341,
  3801,
  3335,
  1261,
  2777,
  3817,
  3347,
  2309,
  4049,
  4024,
  4051,
  4039,
  4270,
  2113,
  3657,
  3555,
  3636,
  2336,
  2299,
  4677,
  4650,
  3878,
  3560,
  3559,
  4058,
  5293,
  4675,
  3637,
  6434,
  4040,
  4678,
  4152,
  2067,
  3877,
  3951,
  3888,
  4724,
  5510,
  7957,
  8726,
  4652,
  9455,
  2340,
  4150,
  6726],
 [4150,
  4677,
  4678,
  4650,
  5293,
  4724,
  6434,
  4675,
  4040,
  4652,
  6112,
  4651,
  4039,
  6432,
  5347,
  4051,
  4148,
  5539,
  5510,
  6296,
  4270,
  6115,
  8558,
  7295,
  2067,
  5535,
  5819,
  8726,
  6848,
  5894,
  6259,
  6114,
  5346,
  5825,
  6113,
  3951,
  8556,
  1449,
  4151,
  5474,
  5966,
  8073,
  7079,
  7553,
  5986,
  8643,
  8554,
  1261,
  4024,
  7294],
 [8726,
  8729,
  3888,
  9594,
  8643,
  9591,
  9588,
  9884,
  2615,
  9585,
  9459,
  9583,
  9581,
  9882,
  9582,
  9458,
  9455,
  8558,
  9349,
  3711,
  9549,
  9584,
  3700,
  2111,
  9265

In [150]:
test_candidate_text = []
for candidate_items in test_candidate_items:
    candidate_item = []
    for item in candidate_items:
        if item_dict[item + 1] in extract_meta_data:
            title = extract_meta_data[item_dict[item + 1]][0]['title']
            candidate_item.append(title)
    test_candidate_text.append(candidate_item)
len(test_candidate_text)

17422

In [214]:
test_prompts_with_candidate = []
test_candidates = []
for items in test_candidate_text:
    candidate_prompts = []
    for idx,item in enumerate(items, start=1):
        candidate_prompts.append(f"{idx}.{item} \n ")
    test_candidates.append(candidate_prompts)
index = 0
test_text_items = []
for items in test_sequences[0]:
    item_prompts = []
    test_text_item = []
    for idx,item in enumerate(items, start=1):
        if item_dict[item] in extract_meta_data:
            title = extract_meta_data[item_dict[item]][0]['title']
            test_text_item.append(title)
            all_items.add(title)
            item_prompts.append(f"{idx}.{title}_{item} \n ")
    test_text_items.append(test_text_item)
    prompt_text = "".join(item_prompts)
    candidate_text = "".join(test_candidates[index])
    test_prompts_with_candidate.append({"Current session interactions": prompt_text, "Candidate item set": candidate_text})
    index += 1
test_text_items

[['Zia Bamboo Exfoliant, 1.6 Ounce Bottles (Pack of 12)'],
 ['Zia Bamboo Exfoliant, 1.6 Ounce Bottles (Pack of 12)',
  'Remington S1051 Salon Quality, Professional Ceramic Hair Straightener'],
 ['Zia Bamboo Exfoliant, 1.6 Ounce Bottles (Pack of 12)',
  'Remington S1051 Salon Quality, Professional Ceramic Hair Straightener',
  'Sunburnt Therapeutic After Sun Relief, 6-Ounce Tube'],
 ['Zia Bamboo Exfoliant, 1.6 Ounce Bottles (Pack of 12)',
  'Remington S1051 Salon Quality, Professional Ceramic Hair Straightener',
  'Sunburnt Therapeutic After Sun Relief, 6-Ounce Tube',
  'Vaseline Men Body and Face Lotion , 20.3 Ounce Bottle (Pack of 3)'],
 ['Zia Bamboo Exfoliant, 1.6 Ounce Bottles (Pack of 12)',
  'Remington S1051 Salon Quality, Professional Ceramic Hair Straightener',
  'Sunburnt Therapeutic After Sun Relief, 6-Ounce Tube',
  'Vaseline Men Body and Face Lotion , 20.3 Ounce Bottle (Pack of 3)',
  'Cotz Pediatric Spf 40, 3.5 Ounce'],
 ['Zia Bamboo Exfoliant, 1.6 Ounce Bottles (Pack of 12

In [140]:
with open('XXXXXXXXXXXXX/train_prompts_with_candidate.json', 'w', encoding='utf-8') as f:
        json.dump(train_prompts_with_candidate, f, ensure_ascii=False, indent=4)

In [145]:
with open('XXXXXXXXXXXXX/test_prompts_with_candidate.json', 'w', encoding='utf-8') as f:
        json.dump(test_prompts_with_candidate, f, ensure_ascii=False, indent=4)

In [223]:
test_prompts = []
index = 0
for items in test_sequences[0]:
    item_prompts = []
    for idx,item in enumerate(items, start=1):
        if item_dict[item] in extract_meta_data:
            title = extract_meta_data[item_dict[item]][0]['title']
            all_items.add(title)
            item_prompts.append(f"{idx}.{title}_{item} \n ")
    prompt_text = "The order in which users click on items is as follows: " + "".join(item_prompts)+ "Candidate item set:" + "".join(test_candidates[index])
    index += 1
    test_prompts.append({"prompt": prompt_text})
test_prompts

[{'prompt': "The order in which users click on items is as follows: 1.Zia Bamboo Exfoliant, 1.6 Ounce Bottles (Pack of 12)_2664 \n Candidate item set:1.Zia Bamboo Exfoliant, 1.6 Ounce Bottles (Pack of 12) \n 2.Bio-Oil, 2-Ounce Bottle \n 3.Clean &amp; Clear Blackhead Eraser Kit \n 4.Axe Detailer Shower Tool-Colors May Vary, 1 Count (Pack of 4) \n 5.Fallene Cotz Plus SPF 58 Water Resistant UVB/UVA Sunscreen for Sensitive Skin, 2.5-Ounce Tube \n 6.Neutrogena Wave Power-Cleanser and Deep Clean Foaming Pads \n 7.Almay Smart Shade Blush, Pink 010, 0.5-Ounce Tubes (Pack of 2) \n 8.Zeno Mini Acne Clearing Device, White \n 9.Nature's Gate Organics Acne Treatment System with Oligopeptide-10, (1 acne treatment system) \n 10.Nivea For Men Energy Hair and Body Wash, 16.9-Ounce Bottle (Pack of 3) \n 11.Yes To Carrots Body Butter, Super Rich, Nourishing, 8.45 Ounce Tubs (Pack of 2) \n 12.Upper Canada Soap And Candle Naturally Whipped Hand Repair, Sweet Vanilla Fig, 4-Ounce Tubes (Pack of 2) \n 13.Ecc

In [152]:
with open('XXXXXXXXXXXX/test_prompts_with_candidate.json', 'w', encoding='utf-8') as f:
        json.dump(test_prompts, f, ensure_ascii=False, indent=4)

In [222]:
all_text_items = []
all_text_items.append(train_text_items)
all_text_items.append(test_text_items)

158717

In [220]:
with open('XXXXXXXXXXXXa/all_text_items1.txt', 'wb') as f:
    pickle.dump(all_text_items, f)